In [1]:
import json
import subprocess
import os

import altair as alt
import pandas as pd
from tqdm.notebook import tqdm

In [2]:
# alt.data_transformers.enable('csv')
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

In [3]:
ips = [
    "34.121.51.252",
    "34.27.25.196",
    "35.239.96.48",
    "34.70.74.250",
    "34.170.237.183",
    "34.69.129.190",
    "35.223.243.136",
]

In [4]:
# for ip in tqdm(ips):
#     process = subprocess.Popen(f'scp -o StrictHostKeyChecking=no -o UserKnownHostsFile=/dev/null chanwutk@{ip}:"/home/chanwutk/code/apperception/outputs/*" ../outputs/', shell=True)
#     process.wait()

In [5]:
DATA_DIR = '../outputs'

In [6]:
failed_videos = {}
for f in os.listdir(DATA_DIR):
    if not f.startswith('failed_videos'): continue

    with open(os.path.join(DATA_DIR, f), 'r') as _f:
        content = json.load(_f)

    name = f[len('failed_videos--'):-len('.json')]
    failed_videos[name] = []
    for v_name, err in content:
        failed_videos[name].append(v_name)

In [7]:
stage_order = [
    'InView', 'DecodeFrame', 'Detection2D.YoloDetection', 'Detection2D.ObjectTypeFilter',
    'DepthEstimation', 'Detection3D.FromDetection2DAndDepth', 'Detection3D.FromDetection2DAndRoad',
    'DetectionEstimation', 'Tracking2D.StrongSORT', 'Tracking3D.FromTracking2DAndDepth',
    'Tracking3D.FromTracking2DAndRoad', 'SegmentTrajectory.FromTracking3D'
]

test_names = {
    'de': 'Only Detection Estimation',
    'noopt': 'Baseline',
    'inview': 'Only In-View',
    'geo': 'Only Geo Depth Estimation',
    'objectfilter': 'Only Object Filter',
    'opt': 'Optimized',
    'optde': 'Optimized with Detection Estimation'
}

test_order = [
    'noopt',
    'inview',
    'objectfilter',
    'geo',
    'de',
    'opt',
    'optde'
]

In [8]:
def combine_perf():
    data = []
    for filename in os.listdir(DATA_DIR):
        if filename.startswith('perf'):
            test, run = filename.split("--")[1].split(".")[0].split("_")
            with open(os.path.join(DATA_DIR, filename), 'r') as f:
                for stage in json.load(f):
                    stagename = stage['stage']
                    for b in stage['benchmark']:
                        after, before = b['keep']
                        assert after <= before
                        skip = (1. - (after / before)) if before != 0 else 0
                        data.append({
                            **b,
                            'stage': stagename,
                            '_test': test,
                            'test': test_names[test],
                            'test_order': test_order.index(test),
                            'run': run,
                            'name': b['name'].split('/')[-1].split('.')[0],
                            'skip': skip,
                            'stage_order': stage_order.index(stagename)
                        })
    return data


perf = combine_perf()

In [9]:
# with open('./output/perf.json', 'w') as f:
#     json.dump([p for p in perf if p['run'] == "0"], f, indent=1)

In [10]:
len([p for p in perf if p['run'] == "0"])

32348

In [11]:
perf[0]

{'name': 'boston-seaport-scene-0067-CAM_FRONT',
 'runtime': 0.8860945701599121,
 'keep': [229, 229],
 'stage': 'DecodeFrame',
 '_test': 'geo',
 'test': 'Only Geo Depth Estimation',
 'test_order': 3,
 'run': '0',
 'skip': 0.0,
 'stage_order': 1}

In [12]:
failed_videos

{'objectfilter_1': ['scene-0244-CAM_FRONT_RIGHT'],
 'geo_1': [],
 'optde_1': ['scene-0305-CAM_FRONT_RIGHT',
  'scene-0499-CAM_FRONT',
  'scene-0597-CAM_FRONT',
  'scene-0597-CAM_FRONT_LEFT',
  'scene-0600-CAM_FRONT_LEFT'],
 'objectfilter_0': ['scene-0244-CAM_FRONT_RIGHT'],
 'optde_3': ['scene-0305-CAM_FRONT_RIGHT',
  'scene-0499-CAM_FRONT',
  'scene-0597-CAM_FRONT',
  'scene-0597-CAM_FRONT_LEFT',
  'scene-0600-CAM_FRONT_LEFT'],
 'de_1': ['scene-0499-CAM_FRONT',
  'scene-0499-CAM_FRONT_RIGHT',
  'scene-0499-CAM_FRONT_LEFT',
  'scene-0515-CAM_FRONT',
  'scene-0515-CAM_FRONT_RIGHT',
  'scene-0515-CAM_FRONT_LEFT',
  'scene-0597-CAM_FRONT',
  'scene-0597-CAM_FRONT_RIGHT',
  'scene-0597-CAM_FRONT_LEFT'],
 'optde_0': ['scene-0305-CAM_FRONT_RIGHT',
  'scene-0499-CAM_FRONT',
  'scene-0597-CAM_FRONT',
  'scene-0597-CAM_FRONT_LEFT',
  'scene-0600-CAM_FRONT_LEFT'],
 'inview_1': [],
 'optde_2': ['scene-0305-CAM_FRONT_RIGHT',
  'scene-0499-CAM_FRONT',
  'scene-0597-CAM_FRONT',
  'scene-0597-CAM_FRON

In [13]:
df_perf = pd.DataFrame.from_dict(perf)
df_perf = df_perf[df_perf['run'] == "0"]
df_perf[:20]

name   runtime        keep  \
0         boston-seaport-scene-0067-CAM_FRONT  0.886095  [229, 229]   
1   boston-seaport-scene-0067-CAM_FRONT_RIGHT  0.870649  [229, 229]   
2    boston-seaport-scene-0067-CAM_FRONT_LEFT  0.638359  [230, 230]   
3         boston-seaport-scene-0068-CAM_FRONT  0.567272  [228, 228]   
4   boston-seaport-scene-0068-CAM_FRONT_RIGHT  0.629802  [226, 226]   
5    boston-seaport-scene-0068-CAM_FRONT_LEFT  0.628432  [227, 227]   
6         boston-seaport-scene-0069-CAM_FRONT  0.561942  [228, 228]   
7   boston-seaport-scene-0069-CAM_FRONT_RIGHT  0.681406  [232, 232]   
8    boston-seaport-scene-0069-CAM_FRONT_LEFT  0.609318  [231, 231]   
9         boston-seaport-scene-0072-CAM_FRONT  0.581375  [231, 231]   
10  boston-seaport-scene-0072-CAM_FRONT_RIGHT  0.575148  [229, 229]   
11   boston-seaport-scene-0072-CAM_FRONT_LEFT  0.610634  [230, 230]   
12        boston-seaport-scene-0075-CAM_FRONT  0.612381  [225, 225]   
13  boston-seaport-scene-0075-CAM_FRONT_RIGHT  0.682062  [226, 226]   
14   boston-seaport-scene-0075-CAM_FRONT_LEFT  0.657464  [228, 228]   
15        boston-seaport-scene-0094-CAM_FRONT  0.547682  [233, 233]   
16  boston-seaport-scene-0094-CAM_FRONT_RIGHT  0.593288  [230, 230]   
17   boston-seaport-scene-0094-CAM_FRONT_LEFT  0.568802  [232, 232]   
18        boston-seaport-scene-0096-CAM_FRONT  0.522327  [228, 228]   
19  boston-seaport-scene-0096-CAM_FRONT_RIGHT  0.575930  [226, 226]   

          stage _test                       test  test_order run  skip  \
0   DecodeFrame   geo  Only Geo Depth Estimation           3   0   0.0   
1   DecodeFrame   geo  Only Geo Depth Estimation           3   0   0.0   
2   DecodeFrame   geo  Only Geo Depth Estimation           3   0   0.0   
3   DecodeFrame   geo  Only Geo Depth Estimation           3   0   0.0   
4   DecodeFrame   geo  Only Geo Depth Estimation           3   0   0.0   
5   DecodeFrame   geo  Only Geo Depth Estimation           3   0   0.0   
6   DecodeFrame   geo  Only Geo Depth Estimation           3   0   0.0   
7   DecodeFrame   geo  Only Geo Depth Estimation           3   0   0.0   
8   DecodeFrame   geo  Only Geo Depth Estimation           3   0   0.0   
9   DecodeFrame   geo  Only Geo Depth Estimation           3   0   0.0   
10  DecodeFrame   geo  Only Geo Depth Estimation           3   0   0.0   
11  DecodeFrame   geo  Only Geo Depth Estimation           3   0   0.0   
12  DecodeFrame   geo  Only Geo Depth Estimation           3   0   0.0   
13  DecodeFrame   geo  Only Geo Depth Estimation           3   0   0.0   
14  DecodeFrame   geo  Only Geo Depth Estimation           3   0   0.0   
15  DecodeFrame   geo  Only Geo Depth Estimation           3   0   0.0   
16  DecodeFrame   geo  Only Geo Depth Estimation           3   0   0.0   
17  DecodeFrame   geo  Only Geo Depth Estimation           3   0   0.0   
18  DecodeFrame   geo  Only Geo Depth Estimation           3   0   0.0   
19  DecodeFrame   geo  Only Geo Depth Estimation           3   0   0.0   

    stage_order  
0             1  
1             1  
2             1  
3             1  
4             1  
5             1  
6             1  
7             1  
8             1  
9             1  
10            1  
11            1  
12            1  
13            1  
14            1  
15            1  
16            1  
17            1  
18            1  
19            1

In [14]:
df_perf.groupby(['test', 'stage']).count()

name  \
test                                stage                                       
Baseline                            DecodeFrame                           600   
                                    DepthEstimation                       600   
                                    Detection2D.YoloDetection             600   
                                    Detection3D.FromDetection2DAndDepth   600   
                                    SegmentTrajectory.FromTracking3D      600   
                                    Tracking2D.StrongSORT                 600   
                                    Tracking3D.FromTracking2DAndDepth     600   
Only Detection Estimation           DecodeFrame                           600   
                                    DepthEstimation                       600   
                                    Detection2D.YoloDetection             600   
                                    Detection3D.FromDetection2DAndDepth   600   
                                    DetectionEstimation                   591   
                                    SegmentTrajectory.FromTracking3D      591   
                                    Tracking2D.StrongSORT                 591   
                                    Tracking3D.FromTracking2DAndDepth     591   
Only Geo Depth Estimation           DecodeFrame                           600   
                                    Detection2D.YoloDetection             600   
                                    Detection3D.FromDetection2DAndRoad    600   
                                    SegmentTrajectory.FromTracking3D      600   
                                    Tracking2D.StrongSORT                 600   
                                    Tracking3D.FromTracking2DAndRoad      600   
Only In-View                        DecodeFrame                           600   
                                    DepthEstimation                       600   
                                    Detection2D.YoloDetection             600   
                                    Detection3D.FromDetection2DAndDepth   600   
                                    InView                                600   
                                    SegmentTrajectory.FromTracking3D      600   
                                    Tracking2D.StrongSORT                 600   
                                    Tracking3D.FromTracking2DAndDepth     600   
Only Object Filter                  DecodeFrame                           600   
                                    DepthEstimation                       600   
                                    Detection2D.ObjectTypeFilter          600   
                                    Detection2D.YoloDetection             600   
                                    Detection3D.FromDetection2DAndDepth   600   
                                    SegmentTrajectory.FromTracking3D      599   
                                    Tracking2D.StrongSORT                 600   
                                    Tracking3D.FromTracking2DAndDepth     600   
Optimized                           DecodeFrame                           600   
                                    Detection2D.ObjectTypeFilter          600   
                                    Detection2D.YoloDetection             600   
                                    Detection3D.FromDetection2DAndRoad    600   
                                    InView                                600   
                                    SegmentTrajectory.FromTracking3D      599   
                                    Tracking2D.StrongSORT                 600   
                                    Tracking3D.FromTracking2DAndRoad      600   
Optimized with Detection Estimation DecodeFrame                           600   
                                    Detection2D.ObjectTypeFilter          600   
                                    Detection2D.YoloDetection             600   
                       

In [15]:
(alt.Chart(df_perf)
    .mark_bar()
    .encode(
        x='average(runtime)',
        y=alt.Y('test:O', sort=alt.Sort({'field': 'test_order'})),
        color=alt.Color('stage:N', sort=stage_order),
        order=alt.Order('order:O')
    )
    .properties(height=300, width=800)
)

alt.Chart(...)

In [19]:
df = df_perf[(df_perf.stage == 'DetectionEstimation') | (df_perf.stage == 'Tracking2D.StrongSORT')]
df_noopt = df[df._test == 'noopt']
df_de = df[df._test == 'de']
df_opt = df[df._test == 'opt']
df_optde = df[df._test == 'optde']

In [20]:
len(df_noopt), len(df_de[df_de.run == '0'])

(600, 1182)

In [21]:
df_baseline = (df_noopt[df_noopt.stage == 'Tracking2D.StrongSORT'].set_index('name')
    .join(df_de[df_de.stage == 'Tracking2D.StrongSORT'].set_index('name'), lsuffix="_noOpt", rsuffix="_de", how='inner')
    # .set_index('name')
    .join(df_de[df_de.stage == 'DetectionEstimation'].set_index('name'), lsuffix="_SS", rsuffix="_DE", how='inner')
)[['runtime_noOpt', 'keep_noOpt', 'stage_noOpt', 'runtime_de', 'keep_de', 'stage_de', 'runtime', 'keep', 'stage']]
df_baseline

runtime_noOpt  keep_noOpt  \
name                                                                   
boston-seaport-scene-0067-CAM_FRONT            58.918906  [229, 229]   
boston-seaport-scene-0067-CAM_FRONT_RIGHT      25.186582  [229, 229]   
boston-seaport-scene-0067-CAM_FRONT_LEFT       31.968025  [230, 230]   
boston-seaport-scene-0068-CAM_FRONT            45.621593  [228, 228]   
boston-seaport-scene-0068-CAM_FRONT_RIGHT      63.643900  [226, 226]   
...                                                  ...         ...   
boston-seaport-scene-0914-CAM_FRONT_RIGHT      27.761492  [233, 233]   
boston-seaport-scene-0914-CAM_FRONT_LEFT       51.571983  [233, 233]   
boston-seaport-scene-0915-CAM_FRONT            72.201869  [236, 236]   
boston-seaport-scene-0915-CAM_FRONT_RIGHT      37.194943  [234, 234]   
boston-seaport-scene-0915-CAM_FRONT_LEFT       48.443912  [236, 236]   

                                                     stage_noOpt  runtime_de  \
name                                                                           
boston-seaport-scene-0067-CAM_FRONT        Tracking2D.StrongSORT   48.507348   
boston-seaport-scene-0067-CAM_FRONT_RIGHT  Tracking2D.StrongSORT   25.352107   
boston-seaport-scene-0067-CAM_FRONT_LEFT   Tracking2D.StrongSORT   29.478977   
boston-seaport-scene-0068-CAM_FRONT        Tracking2D.StrongSORT   20.350483   
boston-seaport-scene-0068-CAM_FRONT_RIGHT  Tracking2D.StrongSORT   57.965982   
...                                                          ...         ...   
boston-seaport-scene-0914-CAM_FRONT_RIGHT  Tracking2D.StrongSORT   25.197581   
boston-seaport-scene-0914-CAM_FRONT_LEFT   Tracking2D.StrongSORT   44.265832   
boston-seaport-scene-0915-CAM_FRONT        Tracking2D.StrongSORT   42.139827   
boston-seaport-scene-0915-CAM_FRONT_RIGHT  Tracking2D.StrongSORT   25.146376   
boston-seaport-scene-0915-CAM_FRONT_LEFT   Tracking2D.StrongSORT   21.479065   

                                              keep_de               stage_de  \
name                                                                           
boston-seaport-scene-0067-CAM_FRONT        [175, 175]  Tracking2D.StrongSORT   
boston-seaport-scene-0067-CAM_FRONT_RIGHT  [202, 202]  Tracking2D.StrongSORT   
boston-seaport-scene-0067-CAM_FRONT_LEFT   [202, 202]  Tracking2D.StrongSORT   
boston-seaport-scene-0068-CAM_FRONT        [127, 127]  Tracking2D.StrongSORT   
boston-seaport-scene-0068-CAM_FRONT_RIGHT  [198, 198]  Tracking2D.StrongSORT   
...                                               ...                    ...   
boston-seaport-scene-0914-CAM_FRONT_RIGHT  [189, 189]  Tracking2D.StrongSORT   
boston-seaport-scene-0914-CAM_FRONT_LEFT   [196, 196]  Tracking2D.StrongSORT   
boston-seaport-scene-0915-CAM_FRONT        [148, 148]  Tracking2D.StrongSORT   
boston-seaport-scene-0915-CAM_FRONT_RIGHT  [177, 177]  Tracking2D.StrongSORT   
boston-seaport-scene-0915-CAM_FRONT_LEFT   [141, 141]  Tracking2D.StrongSORT   

                                             runtime        keep  \
name                                                               
boston-seaport-scene-0067-CAM_FRONT        12.888192  [175, 229]   
boston-seaport-scene-0067-CAM_FRONT_RIGHT   4.708537  [202, 229]   
boston-seaport-scene-0067-CAM_FRONT_LEFT    4.899929  [202, 230]   
boston-seaport-scene-0068-CAM_FRONT         4.443251  [127, 228]   
boston-seaport-scene-0068-CAM_FRONT_RIGHT   7.830472  [198, 226]   
...                                              ...         ...   
boston-seaport-scene-0914-CAM_FRONT_RIGHT   3.989206  [189, 233]   
boston-seaport-scene-0914-CAM_FRONT_LEFT    9.480897  [196, 233]   
boston-seaport-scene-0915-CAM_FRONT        12.115072  [148, 236]   
boston-seaport-scene-0915-CAM_FRONT_RIGHT   3.747970  [177, 234]   
boston-seaport-scene-0915-CAM_FRONT_LEFT    5.038727  [141, 236]   

                                                         stage  
name                                                            
boston-se

In [26]:
def _(x):
    return pd.Series(
        [x.runtime_noOpt, x.keep_noOpt[1], x.runtime, x.runtime_de, x.keep[0]],
        index=['runtime_before', 'frames_before', 'runtime_ss_after', 'runtime_de_after', 'frames_after']
    )


df_baseline_ = df_baseline.reset_index().apply(_, axis=1)
df_baseline_

runtime_before  frames_before  runtime_ss_after  runtime_de_after  \
0         58.918906          229.0         12.888192         48.507348   
1         25.186582          229.0          4.708537         25.352107   
2         31.968025          230.0          4.899929         29.478977   
3         45.621593          228.0          4.443251         20.350483   
4         63.643900          226.0          7.830472         57.965982   
..              ...            ...               ...               ...   
586       27.761492          233.0          3.989206         25.197581   
587       51.571983          233.0          9.480897         44.265832   
588       72.201869          236.0         12.115072         42.139827   
589       37.194943          234.0          3.747970         25.146376   
590       48.443912          236.0          5.038727         21.479065   

     frames_after  
0           175.0  
1           202.0  
2           202.0  
3           127.0  
4           198.0  
..            ...  
586         189.0  
587         196.0  
588         148.0  
589         177.0  
590         141.0  

[591 rows x 5 columns]

In [28]:
(alt.Chart(df_baseline_)
    .mark_point()
    .transform_calculate(
        'runtime_reduction',
        calculate='(datum.runtime_ss_after + datum.runtime_de_after) / datum.runtime_before'
    )
    .transform_calculate(
        'frames_reduction',
        calculate='datum.frames_after / datum.frames_before'
    )
    .encode(
        x='frames_reduction:Q',
        y='runtime_reduction:Q',
    )
)

alt.Chart(...)

In [29]:
(alt.Chart(df_baseline_)
    .mark_point()
    .transform_calculate(
        'runtime_reduction',
        calculate='datum.runtime_ss_after / datum.runtime_before'
    )
    .transform_calculate(
        'frames_reduction',
        calculate='datum.frames_after / datum.frames_before'
    )
    .encode(
        x='frames_reduction:Q',
        y='runtime_reduction:Q',
    )
)

alt.Chart(...)

In [30]:
(alt.Chart(df_baseline_)
    .mark_point()
    .transform_calculate(
        'runtime_reduction',
        calculate='datum.runtime_de_after / datum.runtime_before'
    )
    .transform_calculate(
        'frames_reduction',
        calculate='datum.frames_after / datum.frames_before'
    )
    .encode(
        x='frames_reduction:Q',
        y='runtime_reduction:Q',
    )
)

alt.Chart(...)